In [1]:
import numpy as np
import pandas as pd
import faiss
from sentence_transformers import SentenceTransformer
from sentence_transformers import InputExample
from torch.utils.data import DataLoader
from sentence_transformers.losses import CosineSimilarityLoss
from datasets import Dataset
import warnings
import time
from itertools import combinations
from tqdm import tqdm
import os
import random
import torch
warnings.filterwarnings("ignore")

In [2]:
for dirname, _, filenames in os.walk('./data/'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

./data/aisles.csv
./data/departments.csv
./data/orders.csv
./data/order_products__prior.csv
./data/order_products__train.csv
./data/products.csv
./data/.ipynb_checkpoints\aisles-checkpoint.csv


In [3]:
for dirname, _, filenames in os.walk('./results/'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

./results/fine_tuned_sentence_bert_FAISS_recommendation.csv
./results/fine_tuned_sentence_bert_product_embeddings.csv
./results/product_features.pkl
./results/product_ids.npy
./results/product_index.faiss
./results/product_pairs_for_finetune.csv
./results/user_features.pkl
./results/user_product_features.pkl
./results/fine_tuned_model\config.json
./results/fine_tuned_model\config_sentence_transformers.json
./results/fine_tuned_model\model.safetensors
./results/fine_tuned_model\modules.json
./results/fine_tuned_model\README.md
./results/fine_tuned_model\sentence_bert_config.json
./results/fine_tuned_model\special_tokens_map.json
./results/fine_tuned_model\tokenizer.json
./results/fine_tuned_model\tokenizer_config.json
./results/fine_tuned_model\vocab.txt
./results/fine_tuned_model\1_Pooling\config.json


# Sentence Bert

Use the "distilbert-base-nli-mean-tokens" model from the sentence-transformers library, which is optimized specifically for sentence similarity tasks.

Compared to the BERT model, Sentence Bert is lighter and more suitable for similarity search.

In [4]:
read_path = './data/'
save_path = './results/'
df_products = pd.read_csv(read_path+'products.csv')

In [5]:
embedding_size = 768
batch_size = 80
avg_bits = 12
compressed_embedding_size = embedding_size//avg_bits  #64-dimensional embedding

In [7]:
# Load pre-trained model to CPU
model = SentenceTransformer('distilbert-base-nli-mean-tokens')

# Creating Mappings from Product ID to Name 
product_map = dict(zip(df_products.product_id, df_products.product_name))

# Generate Fine Tuning Data

Construct positive and negative sample pairs. The pairs with the same aisle are positive samples, and the pairs with different aisles are negative samples.

In [11]:
df_prod_train = df_products.sample(frac=0.8, random_state=42)
df_prod_test = df_products.drop(df_prod_train.index)

In [12]:
df_prod_train.head(3)

product_id                                 product_name  aisle_id  \
33626       33627                                  Mix Popcorn       107   
18192       18193                    Tangerine Lime Drink Tabs       100   
47099       47100  Fire Roasted Diced Tomatoes With Seasonings        81   

       department_id  
33626             19  
18192             21  
47099             15

In [14]:
# To speed up sampling, construct lookup
aisle_groups = df_prod_train.groupby("aisle_id")

positive_pairs = []
negative_pairs = []

# Constructing positive samples: two-by-two combinations within the same aisle_id
for aisle_id, group in tqdm(aisle_groups, desc="Positive sample construction"):
    names = group["product_name"].unique().tolist()
    if len(names) < 2:
        continue
    combs = list(combinations(names, 2))
    sampled = random.sample(combs, min(50, len(combs)))  # control quantity
    for name1, name2 in sampled:
        positive_pairs.append((name1, name2, 1))

# Construct negative samples: take one product combination under each different aisle_id.
product_by_aisle = {
    aisle_id: group["product_name"].tolist()
    for aisle_id, group in aisle_groups
    if len(group) >= 2
}

aisles = list(product_by_aisle.keys())
for _ in tqdm(range(len(positive_pairs)), desc="Negative sample construction"):  # Keeping positive and negative quantities consistent
    d1, d2 = random.sample(aisles, 2)
    p1 = random.choice(product_by_aisle[d1])
    p2 = random.choice(product_by_aisle[d2])
    negative_pairs.append((p1, p2, 0))

# Combining positive and negative samples
df_pairs = pd.DataFrame(positive_pairs + negative_pairs, columns=["product_1", "product_2", "label"])
df_pairs = df_pairs.sample(frac=1).reset_index(drop=True)  # Shuffle the order

# preserve
df_pairs.to_csv(save_path+"product_pairs_for_finetune.csv", index=False)
print("Sample construction is complete and the total number of samples generated is ", len(df_pairs))


Positive sample construction: 100%|█| 134/134 [00:00<00:00, 135
Negative sample construction: 100%|█| 6686/6686 [00:00<00:00, 2

Sample construction is complete and the total number of samples generated is  13372


# Fine Tuning

In [17]:
df_pairs = pd.read_csv(save_path+"product_pairs_for_finetune.csv")

train_examples = [
    InputExample(texts=[row['product_1'], row['product_2']], label=float(row['label']))
    for _, row in df_pairs.iterrows()
]

# Build a training data loader
train_dataloader = DataLoader(train_examples, shuffle=True, batch_size=64)

# Define the loss function (contrast learning)
# You can also choose TripletLoss, ContrastiveLoss, etc., which are suitable for data with triplets.
train_loss = CosineSimilarityLoss(model=model)

In [18]:
model_save_path = save_path+'fine_tuned_model'

In [ ]:
# Fine tuning
# Running time is 2:20:20.
start = time.time()
os.environ["WANDB_DISABLED"] = "true" # Disable wandb logging
model.fit(
    train_objectives=[(train_dataloader, train_loss)],
    epochs=3,
    warmup_steps=100,
    output_path=model_save_path  # Save path of the fine-tuned model
)
end = time.time()
print('Running time is {:.2f} seconds.'.format(end-start))

# Use Fine Tuned Model

In [21]:
# Loading the fine-tuned model
model = SentenceTransformer(model_save_path)

In [22]:
# Generate embeddings
def generate_embeddings(texts, batch_size=64):
    embeddings = []
    for i in range(0, len(texts), batch_size):
        batch = texts[i:i+batch_size]
        batch_emb = model.encode(batch, show_progress_bar=True)
        embeddings.append(batch_emb)
    return np.vstack(embeddings)

In [23]:
# Generate embeddings for all products
# Running time is 22 minutes.
start = time.time()
product_embeddings = generate_embeddings(df_products.product_name.tolist())
end = time.time()
print('Running time is {:.2f} seconds.'.format(end-start))

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Running time is 499.88 seconds.


In [24]:
product_embeddings

array([[-0.7822997 , -0.04733571,  0.58125   , ...,  0.2568811 ,
         0.19583574,  0.26452616],
       [-0.7109628 , -0.68969625,  0.6558963 , ..., -0.19502588,
         0.3013938 ,  0.37189934],
       [-1.5615875 , -0.34351274,  0.6264252 , ..., -0.78111786,
        -0.07937897,  0.20895328],
       ...,
       [-0.4367219 ,  0.4119987 ,  0.15365565, ..., -0.17477854,
         0.89545554, -0.01979799],
       [-0.43966573, -0.35076368,  0.19027981, ..., -0.8771781 ,
         0.48300275, -0.5072088 ],
       [-0.3744227 , -0.66385657,  0.9300187 , ..., -0.44701144,
         0.16792175,  0.5216728 ]], dtype=float32)

In [25]:
embeddings_df = pd.DataFrame(product_embeddings, columns=[i for i in range(product_embeddings.shape[1])])

# If the original product name needs to be preserved, a column can be added
embeddings_df['product_id'] = df_products['product_id'].values
embeddings_df['product_name'] = df_products['product_name'].values

# Save to CSV file
embeddings_df.to_csv(save_path+'fine_tuned_sentence_bert_product_embeddings.csv', index=False)

# FAISS-cpu

In [27]:
# Create FAISS indexes
dimension = product_embeddings.shape[1]  # Dimensions of embedded vectors
index = faiss.IndexFlatL2(dimension)  # L2 distance (Euclidean distance)

# Adding vectors to indexes
index.add(product_embeddings)

# Save index and product ID mapping
faiss.write_index(index, save_path+"product_index.faiss")
np.save(save_path+"product_ids.npy", df_products.product_id.values)


# Loading Indexes and Product IDs
index = faiss.read_index(save_path+"product_index.faiss")
product_ids = np.load(save_path+"product_ids.npy")

In [28]:
# Recommended Similar Product Functions with CPU
def recommend_similar_products(query, k=5):
    # Generate query text embedding
    query_embedding = model.encode([query])

    # Search for the most similar k products
    distances, indices = index.search(query_embedding, k)

    # Get product ID and name
    similar_ids = product_ids[indices[0]]
    similar_products = [product_map[pid] for pid in similar_ids]

    return list(zip(similar_ids, similar_products, distances[0]))

In [29]:
# Test the recommendation function
# CPU
# Running time is 1 hour.
start = time.time()
k_ = 21
df_recom = pd.DataFrame()
for ix,row in df_products.iterrows():
    tmp_dict = {"product_id": row['product_id'], 'product_name':row['product_name']}

    query_product = row['product_name']
    recommendations = recommend_similar_products(query_product, k=k_)
    for i, (pid, name, dist) in enumerate(recommendations, 0):
        tmp_dict['nearest_'+str(i)] = name
    df_recom = pd.concat([df_recom,pd.Series(tmp_dict).to_frame().T])
end = time.time()
print('Running time is {:.2f} seconds.'.format(end-start))

Running time is 3127.95 seconds.


In [30]:
df_recom.head(5)

product_id                                       product_name  \
0           1                         Chocolate Sandwich Cookies   
0           2                                   All-Seasons Salt   
0           3               Robust Golden Unsweetened Oolong Tea   
0           4  Smart Ones Classic Favorites Mini Rigatoni Wit...   
0           5                          Green Chile Anytime Sauce   
..        ...                                                ...   
0       49684          Vodka, Triple Distilled, Twist of Vanilla   
0       49685                 En Croute Roast Hazelnut Cranberry   
0       49686                                   Artisan Baguette   
0       49687         Smartblend Healthy Metabolism Dry Cat Food   
0       49688                             Fresh Foaming Cleanser   

                                            nearest_0  \
0                          Chocolate Sandwich Cookies   
0                                    All-Seasons Salt   
0                Robust Golden Unsweetened Oolong Tea   
0   Smart Ones Classic Favorites Mini Rigatoni Wit...   
0                           Green Chile Anytime Sauce   
..                                                ...   
0           Vodka, Triple Distilled, Twist of Vanilla   
0                  En Croute Roast Hazelnut Cranberry   
0                                    Artisan Baguette   
0          Smartblend Healthy Metabolism Dry Cat Food   
0                              Fresh Foaming Cleanser   

                                      nearest_1  \
0              Chocolate Creme Sandwich Cookies   
0                                    Epsom Salt   
0                 Unsweetened Golden Oolong Tea   
0   Gluten-Free Yellow Cheddar Cheese Sauce Mix   
0              Mild Enchilada Green Chile Sauce   
..                                          ...   
0                           Whipped Cream Vodka   
0                        Peppercorn Cashew Brie   
0                 Sprouted Seven-Grain Baguette   
0   ProActive Health Adult Chicken Dry Cat Food   
0             Clear Complexion Foaming Cleanser   

                                 nearest_2  \
0   Chocolate Berry Creme Sandwich Cookies   
0                 Season All Seasoned Salt   
0                    Unsweetened Black Tea   
0               Creamy Vodka Italian Sauce   
0              Green Chile Enchilada Sauce   
..                                     ...   
0                     Vodka, Pear Flavored   
0             New England Cranberry Relish   
0                      Multigrain Baguette   
0        Adult Healthy Metabolism Cat Food   
0                          Liquid Cleanser   

                                            nearest_3  \
0                            Vanilla Sandwich Cookies   
0                                          Table Salt   
0                   Earl Grey Decaffeinated Black Tea   
0            Riserva Artichokes & Asiago Cheese Sauce   
0                  Green Chile Medium Enchilada Sauce   
..                                                ...   
0                            Sweet Tea Flavored Vodka   
0                  Unsweetened Cinnamon Raisin Muesli   
0                                            Baguette   
0   ProActive Health Adult Weight Control Dry Cat ...   
0         Good & Clean - Daily Detox Foaming Cleanser   

                                            nearest_4  \
0               Chocolate Mint Creme Sandwich Cookies   
0                                 Lavender Epsom Salt   
0                          Just Green Unsweetened Tea   
0   In a creamy sauce, topped with aged parmesan c...   
0                    Mild Green Chile Enchilada Sauce   
..                                                ...   
0                  Flavored Vodka, Twist of Raspberry   
0                            Organic Raspberry Muesli   
0                                     Rustic Baguette   
0               Healthy Naturals Chicken Dry Cat Food   
0                      

In [31]:
df_recom.to_csv(save_path+"fine_tuned_sentence_bert_FAISS_recommendation.csv",index=None)